# Муравьиные алгоритмы для решения задачи коммивояжера
### Визуализация поиска решения и анализ качества алгоритма

Для построение графиков и анимаций будем использовать библиотеки `matplotlib` и `plotly.graph_objects`. 
Добавим все необходимые библиотеки.

In [1]:
import pandas as pd
import plotly.graph_objects as go

from algorithms.ant import AntColony
from tsp import TSP
from typing import List

Создадим функцию для сохранения информации о городах для TSP из текстового файла в `DataFrame`

In [2]:
def get_cities_df(file_path: str):
    cities_df = pd.read_csv(file_path, sep=' ', header=None)
    cities_df.columns = ['name', 'x', 'y']
    return cities_df

In [3]:
file_path = 'tests/50cities_1.txt'
cities_df = get_cities_df(file_path)

Посмотрим на сохраненный нами тест для 16 городов.

In [4]:
cities_df

name    x    y
0      1  230  166
1      2   92   66
2      3   39   47
3      4  218  207
4      5   64  197
5      6  133  130
6      7  238   91
7      8  194    7
8      9   14  222
9     10  127  104
10    11  128  194
11    12  170  220
12    13    5   68
13    14  164   19
14    15   21   82
15    16   66  179
16    17  107  189
17    18   29  239
18    19   63   69
19    20   79  156
20    21  117   29
21    22   45    2
22    23  139  190
23    24  133   55
24    25  196  197
25    26   68  136
26    27  158  205
27    28  228  183
28    29  107   77
29    30   95   63
30    31  195   86
31    32  245  244
32    33  196  154
33    34  190  241
34    35  216  116
35    36  204   58
36    37  200  234
37    38  164  110
38    39  241   73
39    40  222  222
40    41   46   52
41    42   79   48
42    43  184  114
43    44  205  194
44    45  172  102
45    46  192   65
46    47  204  115
47    48  183  155
48    49    5  200
49    50  116  159

Напишем функцию инициализации задачи коммивояжера

In [5]:
def init_tsp(cities_df: pd.DataFrame):
    cities: List[TSP.City] = []
    for _, row in cities_df.iterrows():
        id, x, y = row['name'], row['x'], row['y']
        cities.append(TSP.City(id, int(x), int(y)))
    return TSP(cities)

Теперь передадим задачу в муравьиный алгоритм и запустим ее

In [6]:
tsp = init_tsp(cities_df)

as_settings = AntColony.Settings()
as_colony = AntColony(AntColony.Variation.ANT_SYSTEM, as_settings)

In [7]:
%%time
dist = as_colony.solve(tsp.cities_amount, tsp.State, tsp.successors, 
                       tsp.goal, tsp.add_to_history, tsp.add_iteration)

print("Ant System: ", dist)

Ant System:  1741.5055458105883
CPU times: user 2min 21s, sys: 499 ms, total: 2min 21s
Wall time: 2min 21s


Реализуем функцию, которая будет рисовать график-анимацию нахождения решения

In [12]:
def plot_tsp(cities_df, tsp, title):
    points = go.Scatter(x=cities_df['x'], y=cities_df['y'], mode='markers',
                        marker=dict(color='#5D69B1', size=10), name='Город',
                        text = ["Название: {}".format(name) for name in cities_df['name'] ])

    paths_history, distances_history = tsp.get_solutions_history()
    answer = paths_history[-1]

    path = go.Scatter(x=answer[0], y=answer[1], mode='lines', name="Маршрут")

    button = {
            "type": "buttons",
            "buttons": [
                {
                    "label": "Запустить",
                    "method": "animate",
                    "args": [None, {"frame": {"duration": 180}}],
                }
            ],
        }

    frames = []
    for i in range(len(paths_history)):
        path = go.Scatter(x=paths_history[i][0], y=paths_history[i][1], mode='lines', name="Маршрут")
        layout = go.Layout(updatemenus=[button], 
                           title_text=f"Маршрут, найденный {title} за {i + 1} итераций, " +
                                      f"длина маршрута = {distances_history[i]}")
        frame = go.Frame(data=[points, path], layout=layout)
        frames.append(frame)


    fig = go.Figure(data=[points, path], frames=frames, layout=layout)
    fig.show()

In [13]:
plot_tsp(cities_df, tsp, "Ant System")

Теперь мы можем собрать все в одну функцию, которая по пути к файлу будет строить график-анимацию. Более того, нами были реализованы различные модификации муравьиного алгоритма (помимо муравьиной системы "Ant System"), поэтому в функции мы будем принимать экземпляр класса `AntColony` с выставленными настройками, то есть с выбором модификации, и заданными параметрами.

In [17]:
def get_solution(file_path: str, ant_colony: AntColony, title: str):
    cities_df = get_cities_df(file_path)
    tsp = init_tsp(cities_df)
    ant_colony.solve(tsp.cities_amount, tsp.State, tsp.successors, 
                     tsp.goal, tsp.add_to_history, tsp.add_iteration)
    plot_tsp(cities_df, tsp, title)

In [37]:
file_path = 'tests/50cities_1.txt'
as_settings = AntColony.Settings(alpha=0.1, beta=1, ants=2, iterations=50)
as_colony = AntColony(AntColony.Variation.ANT_SYSTEM, as_settings)

get_solution(file_path, as_colony, 'Ant System')